In [1]:
import torch
import numpy as np
from omegaconf import DictConfig, OmegaConf
from mytest.RoseTTAFoldModel import RoseTTAFoldModule
from rfdiffusion.kinematics import get_init_xyz, xyz_to_t2d
from mytest.diffusion import Diffuser
from rfdiffusion.chemical import seq2chars
from rfdiffusion.util_module import ComputeAllAtomCoords
from rfdiffusion.contigs import ContigMap
from rfdiffusion.inference import utils as iu, symmetry
from rfdiffusion.potentials.manager import PotentialManager
import logging
import torch.nn.functional as nn
from rfdiffusion import util
from hydra.core.hydra_config import HydraConfig
import os

from rfdiffusion.model_input_logger import pickle_function_call
import sys

from rfdiffusion.inference import model_runners
import re
import os, time, pickle
import torch
from omegaconf import OmegaConf
import hydra
import logging
from rfdiffusion.util import writepdb_multi, writepdb
from rfdiffusion.inference import utils as iu
from hydra.core.hydra_config import HydraConfig
import numpy as np
import random
import glob


/WORK/PUBLIC/lulei_work/xjt/Protein_design/RFdiffusion/rfdiffusion/util.py:253: UserWarning: Using torch.cross without specifying the dim arg is deprecated.
Please either pass the dim explicitly or simply use torch.linalg.cross.
The default value of dim will change to agree with that of linalg.cross in a future release. (Triggered internally at /pytorch/aten/src/ATen/native/Cross.cpp:62.)
  Z = torch.cross(Xn, Yn)
/home/fit/lulei/WORK/.conda/envs/SE3nv/lib/python3.9/site-packages/dgl/backend/pytorch/sparse.py:104: FutureWarning: `torch.cuda.amp.custom_fwd(args...)` is deprecated. Please use `torch.amp.custom_fwd(args..., device_type='cuda')` instead.
  @custom_fwd(cast_inputs=th.float16)
/home/fit/lulei/WORK/.conda/envs/SE3nv/lib/python3.9/site-packages/dgl/backend/pytorch/sparse.py:128: FutureWarning: `torch.cuda.amp.custom_bwd(args...)` is deprecated. Please use `torch.amp.custom_bwd(args..., device_type='cuda')` instead.
  def backward(ctx, dZ):
/home/fit/lulei/WORK/.conda/envs/SE3n

t1d 时间特征加的很奇怪
    # Set timestep feature to 1 where diffusion mask is True, else 1-t/T
    timefeature = torch.zeros((L)).float()
    timefeature[self.mask_str.squeeze()] = 1
    timefeature[~self.mask_str.squeeze()] = 1 - t/self.T
    timefeature = timefeature[None,None,...,None]

t2d = 
def xyz_to_t2d(xyz_t, params=PARAMS):
    """convert template cartesian coordinates into 2d distance 
    and orientation maps
    
    Parameters
    ----------
    xyz_t : pytorch tensor of shape [batch,templ,nres,3,3]
            stores Cartesian coordinates of template backbone N,Ca,C atoms

    Returns
    -------
    t2d : pytorch tensor of shape [batch,nres,nres,37+6+3]
          stores stacked dist,omega,theta,phi 2D maps 
    """

In [2]:
SCRIPT_DIR=os.getcwd()

TOR_INDICES  = util.torsion_indices
TOR_CAN_FLIP = util.torsion_can_flip
REF_ANGLES   = util.reference_angles

class MySampler:

    def __init__(self, conf: DictConfig):
        """
        Initialize sampler.
        Args:
            conf: Configuration.
        """
        self.initialized = False
        self.initialize(conf)
        
    def initialize(self, conf: DictConfig) -> None:
        """
        Initialize sampler.
        Args:
            conf: Configuration
        
        - Selects appropriate model from input
        - Assembles Config from model checkpoint and command line overrides

        """
        self._log = logging.getLogger(__name__)
        if torch.cuda.is_available():
            self.device = torch.device('cuda')
        else:
            self.device = torch.device('cpu')
        needs_model_reload = not self.initialized or conf.inference.ckpt_override_path != self._conf.inference.ckpt_override_path

        # Assign config to Sampler
        self._conf = conf

        ################################
        ### Select Appropriate Model ###
        ################################

        if conf.inference.model_directory_path is not None:
            model_directory = conf.inference.model_directory_path
        else:
            model_directory = f"{SCRIPT_DIR}/../models"

        print(f"Reading models from {model_directory}")

        # Initialize inference only helper objects to Sampler
        if conf.inference.ckpt_override_path is not None:
            self.ckpt_path = conf.inference.ckpt_override_path
            print("WARNING: You're overriding the checkpoint path from the defaults. Check that the model you're providing can run with the inputs you're providing.")
        else:
            if conf.contigmap.inpaint_seq is not None or conf.contigmap.provide_seq is not None or conf.contigmap.inpaint_str:
                # use model trained for inpaint_seq
                if conf.contigmap.provide_seq is not None:
                    # this is only used for partial diffusion
                    assert conf.diffuser.partial_T is not None, "The provide_seq input is specifically for partial diffusion"
                if conf.scaffoldguided.scaffoldguided:
                    self.ckpt_path = f'{model_directory}/InpaintSeq_Fold_ckpt.pt'
                else:
                    self.ckpt_path = f'{model_directory}/InpaintSeq_ckpt.pt'
            elif conf.ppi.hotspot_res is not None and conf.scaffoldguided.scaffoldguided is False:
                # use complex trained model
                self.ckpt_path = f'{model_directory}/Complex_base_ckpt.pt'
            elif conf.scaffoldguided.scaffoldguided is True:
                # use complex and secondary structure-guided model
                self.ckpt_path = f'{model_directory}/Complex_Fold_base_ckpt.pt'
            else:
                # use default model
                self.ckpt_path = f'{model_directory}/Base_ckpt.pt'
        # for saving in trb file:
        assert self._conf.inference.trb_save_ckpt_path is None, "trb_save_ckpt_path is not the place to specify an input model. Specify in inference.ckpt_override_path"
        self._conf['inference']['trb_save_ckpt_path']=self.ckpt_path

        #######################
        ### Assemble Config ###
        #######################

        if needs_model_reload:
            # Load checkpoint, so that we can assemble the config
            self.load_checkpoint()
            #self.assemble_config_from_chk()
            # Now actually load the model weights into RF
            self.model = self.load_model()
        else:
            self.assemble_config_from_chk()

        # self.initialize_sampler(conf)
        self.initialized=True

        # Initialize helper objects
        self.inf_conf = self._conf.inference
        self.contig_conf = self._conf.contigmap
        self.denoiser_conf = self._conf.denoiser
        self.ppi_conf = self._conf.ppi
        self.potential_conf = self._conf.potentials
        self.diffuser_conf = self._conf.diffuser
        self.preprocess_conf = self._conf.preprocess

        if conf.inference.schedule_directory_path is not None:
            schedule_directory = conf.inference.schedule_directory_path
        else:
            schedule_directory = "cache"

        # Check for cache schedule
        if not os.path.exists(schedule_directory):
            os.mkdir(schedule_directory)
        self.diffuser = Diffuser(**self._conf.diffuser, device = self.device,cache_dir=schedule_directory)

        ###########################
        ### Initialise Symmetry ###
        ###########################

        if self.inf_conf.symmetry is not None:
            self.symmetry = symmetry.SymGen(
                self.inf_conf.symmetry,
                self.inf_conf.recenter,
                self.inf_conf.radius,
                self.inf_conf.model_only_neighbors,
            )
        else:
            self.symmetry = None

        self.allatom = ComputeAllAtomCoords().to(self.device)
        
        if self.inf_conf.input_pdb is None:
            # set default pdb
            script_dir = os.getcwd()
            self.inf_conf.input_pdb=os.path.join(script_dir, '../examples/input_pdbs/1qys.pdb')
        self.target_feats = iu.process_target(self.inf_conf.input_pdb, parse_hetatom=True, center=False)
        self.chain_idx = None

        ##############################
        ### Handle Partial Noising ###
        ##############################

        if self.diffuser_conf.partial_T:
            assert self.diffuser_conf.partial_T <= self.diffuser_conf.T
            self.t_step_input = int(self.diffuser_conf.partial_T)
        else:
            self.t_step_input = int(self.diffuser_conf.T)
        
    @property
    def T(self):
        '''
            Return the maximum number of timesteps
            that this design protocol will perform.

            Output:
                T (int): The maximum number of timesteps to perform
        '''
        return self.diffuser_conf.T

    def load_checkpoint(self) -> None:
        """Loads RF checkpoint, from which config can be generated."""
        self._log.info(f'Reading checkpoint from {self.ckpt_path}')
        print('This is inf_conf.ckpt_path')
        print(self.ckpt_path)
        self.ckpt  = torch.load(
            self.ckpt_path, map_location=self.device)

    def assemble_config_from_chk(self) -> None:
        """
        Function for loading model config from checkpoint directly.

        Takes:
            - config file

        Actions:
            - Replaces all -model and -diffuser items
            - Throws a warning if there are items in -model and -diffuser that aren't in the checkpoint
        
        This throws an error if there is a flag in the checkpoint 'config_dict' that isn't in the inference config.
        This should ensure that whenever a feature is added in the training setup, it is accounted for in the inference script.

        """
        # get overrides to re-apply after building the config from the checkpoint
        overrides = []
        if HydraConfig.initialized():
            overrides = HydraConfig.get().overrides.task
        print("Assembling -model, -diffuser and -preprocess configs from checkpoint")

        for cat in ['model','diffuser','preprocess']:
            for key in self._conf[cat]:
                try:
                    print(f"USING MODEL CONFIG: self._conf[{cat}][{key}] = {self.ckpt['config_dict'][cat][key]}")
                    self._conf[cat][key] = self.ckpt['config_dict'][cat][key]
                except:
                    pass
        
        # add overrides back in again
        for override in overrides:
            if override.split(".")[0] in ['model','diffuser','preprocess']:
                print(f'WARNING: You are changing {override.split("=")[0]} from the value this model was trained with. Are you sure you know what you are doing?') 
                mytype = type(self._conf[override.split(".")[0]][override.split(".")[1].split("=")[0]])
                self._conf[override.split(".")[0]][override.split(".")[1].split("=")[0]] = mytype(override.split("=")[1])

    def load_model(self):
        """Create RosettaFold model from preloaded checkpoint."""
        
        # Read input dimensions from checkpoint.
        self.d_t1d=self._conf.preprocess.d_t1d
        self.d_t2d=self._conf.preprocess.d_t2d
        model = RoseTTAFoldModule(**self._conf.model, d_t1d=self.d_t1d, d_t2d=self.d_t2d, T=self._conf.diffuser.T).to(self.device)
        if self._conf.logging.inputs:
            pickle_dir = pickle_function_call(model, 'forward', 'inference')
            print(f'pickle_dir: {pickle_dir}')
        model = model.eval()
        self._log.info(f'Loading checkpoint.')
        model.load_state_dict(self.ckpt['model_state_dict'], strict=False)
        return model

    def construct_contig(self, target_feats):
        """
        Construct contig class describing the protein to be generated
        """
        self._log.info(f'Using contig: {self.contig_conf.contigs}')
        return ContigMap(target_feats, **self.contig_conf)

    def construct_denoiser(self, L, visible):
        """Make length-specific denoiser."""
        denoise_kwargs = OmegaConf.to_container(self.diffuser_conf)
        denoise_kwargs.update(OmegaConf.to_container(self.denoiser_conf))
        denoise_kwargs.update({
            'L': L,
            'diffuser': self.diffuser,
            'potential_manager': self.potential_manager,
        })
        return iu.Denoise(**denoise_kwargs)
    
    def sample_init_forward(self, xyz_3, seq_orig,partial_T=None, mask=None,return_forward_trajectory=False):
        """
        Arg :
            xyz_3: (B, L, 3, 3) Initial coordinates of the protein (N, CA, C).
            seq_orig: (B, L) Original sequence of the protein.
            partial_T: (int) If provided, will perform partial diffusion from the given coordinates.


        Initial features to start the sampling process.
        
        Modify signature and function body for different initialization
        based on the config.
        
        Returns:
            xt: Starting positions with a portion of them randomly sampled.
            seq_t: Starting sequence with a portion of them set to unknown.
        """
        

        ###################################
        ### Initialize other attributes ###
        ###################################

        xyz_3 = xyz_3 # (B, L, 3, 3)
        B , L = xyz_3.shape[:2]
        xyz_27 = torch.full((B,  L, 27, 3), torch.nan, device=xyz_3.device, dtype=torch.float32) 
        xyz_27[:, :, :3, :] = xyz_3

        L_mapped = len(self.contig_map.ref)
        contig_map=self.contig_map

        self.chain_idx=['A' if i < self.binderlen else 'B' for i in range(L_mapped)]
        
        ####################################
        ### Generate initial coordinates ###
        ####################################

        if partial_T != None:
            # assert xyz_27.shape[0] == L_mapped, f"there must be a coordinate in the input PDB for \
            #         each residue implied by the contig string for partial diffusion.  length of \
            #         input PDB != length of contig string: {xyz_27.shape[0]} != {L_mapped}"
            # assert contig_map.hal_idx0 == contig_map.ref_idx0, f'for partial diffusion there can \
            #         be no offset between the index of a residue in the input and the index of the \
            #         residue in the output, {contig_map.hal_idx0} != {contig_map.ref_idx0}'
            # Partially diffusing from a known structure
            xyz_mapped=xyz_27
        else:
            # Fully diffusing from points initialised at the origin
            # adjust size of input xt according to residue map
            xyz_mapped = torch.full((1,1,L_mapped,27,3), np.nan)
            xyz_mapped[:, :, contig_map.hal_idx0, ...] = xyz_27[contig_map.ref_idx0,...]
            xyz_motif_prealign = xyz_mapped.clone()
            motif_prealign_com = xyz_motif_prealign[0,0,:,1].mean(dim=0)
            self.motif_com = xyz_27[contig_map.ref_idx0,1].mean(dim=0)
            xyz_mapped = get_init_xyz(xyz_mapped).squeeze()

        # Diffuse the contig-mapped coordinates 
        if partial_T != None:
            assert partial_T <= self.diffuser_conf.T, "Partial_T must be less than T"
            self.t_step_input = int(partial_T)
        else:
            self.t_step_input = int(self.diffuser_conf.T)
        t_list = np.arange(1, self.t_step_input+1)

        #################################
        ### Generate initial sequence ###
        #################################

        seq_t = torch.full((1,L_mapped), 21).squeeze() # 21 is the mask token
        # seq_t[contig_map.hal_idx0] = seq_orig[contig_map.ref_idx0]

        seq_t[~self.mask_seq.squeeze()] = 21  #21 is motif mask, 20 is batch mask
        seq_t    = torch.nn.functional.one_hot(seq_t, num_classes=22).float() # [B,L,22]
        seq_orig = torch.nn.functional.one_hot(seq_orig, num_classes=22).float() # [B,L,22]
        seq_orig_20 = seq_orig[:,:,:20]
        fa_stack, noised_seq, noised_seq_grad = self.diffuser.diffuse_pose(
            xyz_mapped,
            seq_orig_20,         #no use
            None, #no use 
            diffusion_mask=mask,  #(B,L)
            t_list=t_list)
        xT = fa_stack[:,-1,:,:14,:]
        xt = torch.clone(xT)

        noised_seq=torch.cat( (noised_seq, seq_orig[:,:,20:]), dim=2)

        self.denoiser = self.construct_denoiser(len(self.contig_map.ref), visible=self.mask_seq.squeeze())

        return xt, noised_seq, noised_seq_grad

    def sample_init(self, return_forward_trajectory=False):
        """
        Initial features to start the sampling process.
        
        Modify signature and function body for different initialization
        based on the config.
        
        Returns:
            xt: Starting positions with a portion of them randomly sampled.
            seq_t: Starting sequence with a portion of them set to unknown.
        """
        
        #######################
        ### Parse input pdb ###
        #######################

        self.target_feats = iu.process_target(self.inf_conf.input_pdb, parse_hetatom=True, center=False)

        ################################
        ### Generate specific contig ###
        ################################

        # Generate a specific contig from the range of possibilities specified at input

        self.contig_map = self.construct_contig(self.target_feats)
        self.mappings = self.contig_map.get_mappings()
        self.mask_seq = torch.from_numpy(self.contig_map.inpaint_seq)[None,:]
        self.mask_str = torch.from_numpy(self.contig_map.inpaint_str)[None,:]
        self.binderlen =  len(self.contig_map.inpaint)     

        ####################
        ### Get Hotspots ###
        ####################

        self.hotspot_0idx=iu.get_idx0_hotspots(self.mappings, self.ppi_conf, self.binderlen)


        #####################################
        ### Initialise Potentials Manager ###
        #####################################

        self.potential_manager = PotentialManager(self.potential_conf,
                                                  self.ppi_conf,
                                                  self.diffuser_conf,
                                                  self.inf_conf,
                                                  self.hotspot_0idx,
                                                  self.binderlen)

        ###################################
        ### Initialize other attributes ###
        ###################################

        xyz_27 = self.target_feats['xyz_27']
        mask_27 = self.target_feats['mask_27']
        seq_orig = self.target_feats['seq']
        L_mapped = len(self.contig_map.ref)
        contig_map=self.contig_map

        self.diffusion_mask = self.mask_str
        self.chain_idx=['A' if i < self.binderlen else 'B' for i in range(L_mapped)]
        
        ####################################
        ### Generate initial coordinates ###
        ####################################

        if self.diffuser_conf.partial_T:
            assert xyz_27.shape[0] == L_mapped, f"there must be a coordinate in the input PDB for \
                    each residue implied by the contig string for partial diffusion.  length of \
                    input PDB != length of contig string: {xyz_27.shape[0]} != {L_mapped}"
            assert contig_map.hal_idx0 == contig_map.ref_idx0, f'for partial diffusion there can \
                    be no offset between the index of a residue in the input and the index of the \
                    residue in the output, {contig_map.hal_idx0} != {contig_map.ref_idx0}'
            # Partially diffusing from a known structure
            xyz_mapped=xyz_27
            atom_mask_mapped = mask_27
        else:
            # Fully diffusing from points initialised at the origin
            # adjust size of input xt according to residue map
            xyz_mapped = torch.full((1,1,L_mapped,27,3), np.nan)
            xyz_mapped[:, :, contig_map.hal_idx0, ...] = xyz_27[contig_map.ref_idx0,...]
            xyz_motif_prealign = xyz_mapped.clone()
            motif_prealign_com = xyz_motif_prealign[0,0,:,1].mean(dim=0)
            self.motif_com = xyz_27[contig_map.ref_idx0,1].mean(dim=0)
            xyz_mapped = get_init_xyz(xyz_mapped).squeeze()
            # adjust the size of the input atom map
            atom_mask_mapped = torch.full((L_mapped, 27), False)
            atom_mask_mapped[contig_map.hal_idx0] = mask_27[contig_map.ref_idx0]

        # Diffuse the contig-mapped coordinates 
        if self.diffuser_conf.partial_T:
            assert self.diffuser_conf.partial_T <= self.diffuser_conf.T, "Partial_T must be less than T"
            self.t_step_input = int(self.diffuser_conf.partial_T)
        else:
            self.t_step_input = int(self.diffuser_conf.T)
        t_list = np.arange(1, self.t_step_input+1)

        #################################
        ### Generate initial sequence ###
        #################################

        seq_t = torch.full((1,L_mapped), 21).squeeze() # 21 is the mask token
        seq_t[contig_map.hal_idx0] = seq_orig[contig_map.ref_idx0]
        
        # Unmask sequence if desired
        if self._conf.contigmap.provide_seq is not None:
            seq_t[self.mask_seq.squeeze()] = seq_orig[self.mask_seq.squeeze()] 

        seq_t[~self.mask_seq.squeeze()] = 21
        seq_t    = torch.nn.functional.one_hot(seq_t, num_classes=22).float() # [L,22]
        seq_orig = torch.nn.functional.one_hot(seq_orig, num_classes=22).float() # [L,22]

        # fa_stack, xyz_true,_ = self.diffuser.diffuse_pose(
        #     xyz_mapped,
        #     torch.clone(seq_t),
        #     atom_mask_mapped.squeeze(),
        #     diffusion_mask=self.diffusion_mask.squeeze(),
        #     t_list=t_list)
        # xT = fa_stack[-1].squeeze()[:,:14,:]
        # xt = torch.clone(xT)

        self.denoiser = self.construct_denoiser(len(self.contig_map.ref), visible=self.mask_seq.squeeze())

        ######################
        ### Apply Symmetry ###
        ######################

        if self.symmetry is not None:
            xt, seq_t = self.symmetry.apply_symmetry(xt, seq_t)
        self._log.info(f'Sequence init: {seq2chars(torch.argmax(seq_t, dim=-1))}')
        
        self.msa_prev = None
        self.pair_prev = None
        self.state_prev = None

        #########################################
        ### Parse ligand for ligand potential ###
        #########################################

        if self.potential_conf.guiding_potentials is not None:
            if any(list(filter(lambda x: "substrate_contacts" in x, self.potential_conf.guiding_potentials))):
                assert len(self.target_feats['xyz_het']) > 0, "If you're using the Substrate Contact potential, \
                        you need to make sure there's a ligand in the input_pdb file!"
                het_names = np.array([i['name'].strip() for i in self.target_feats['info_het']])
                xyz_het = self.target_feats['xyz_het'][het_names == self._conf.potentials.substrate]
                xyz_het = torch.from_numpy(xyz_het)
                assert xyz_het.shape[0] > 0, f'expected >0 heteroatoms from ligand with name {self._conf.potentials.substrate}'
                xyz_motif_prealign = xyz_motif_prealign[0,0][self.diffusion_mask.squeeze()]
                motif_prealign_com = xyz_motif_prealign[:,1].mean(dim=0)
                xyz_het_com = xyz_het.mean(dim=0)
                for pot in self.potential_manager.potentials_to_apply:
                    pot.motif_substrate_atoms = xyz_het
                    pot.diffusion_mask = self.diffusion_mask.squeeze()
                    pot.xyz_motif = xyz_motif_prealign
                    pot.diffuser = self.diffuser
        # return xt, seq_t
        return None

    def _preprocess(self, seq, xyz_t, t, repack=False):
        
        """
        Function to prepare inputs to diffusion model
        
            seq (L,22) one-hot sequence 

            msa_masked (1,1,L,48)

            msa_full (1,1,L,25)
        
            xyz_t (L,14,3) template crds (diffused) 

            t1d (1,L,28) this is the t1d before tacking on the chi angles:
                - seq + unknown/mask (21)
                - global timestep (1-t/T if not motif else 1) (1)

                MODEL SPECIFIC:
                - contacting residues: for ppi. Target residues in contact with binder (1)
                - empty feature (legacy) (1)
                - ss (H, E, L, MASK) (4)
            
            t2d (1, L, L, 45)
                - last plane is block adjacency
    """

        L = seq.shape[0]
        T = self.T
        binderlen = self.binderlen
        target_res = self.ppi_conf.hotspot_res

        ##################
        ### msa_masked ###
        ##################
        msa_masked = torch.zeros((1,1,L,48))
        msa_masked[:,:,:,:22] = seq[None, None]
        msa_masked[:,:,:,22:44] = seq[None, None]
        msa_masked[:,:,0,46] = 1.0
        msa_masked[:,:,-1,47] = 1.0

        ################
        ### msa_full ###
        ################
        msa_full = torch.zeros((1,1,L,25))
        msa_full[:,:,:,:22] = seq[None, None]
        msa_full[:,:,0,23] = 1.0
        msa_full[:,:,-1,24] = 1.0

        ###########
        ### t1d ###
        ########### 

        # Here we need to go from one hot with 22 classes to one hot with 21 classes (last plane is missing token)
        t1d = torch.zeros((1,1,L,21))

        seqt1d = torch.clone(seq)
        for idx in range(L):
            if seqt1d[idx,21] == 1:
                seqt1d[idx,20] = 1
                seqt1d[idx,21] = 0
        
        t1d[:,:,:,:21] = seqt1d[None,None,:,:21]
        

        # Set timestep feature to 1 where diffusion mask is True, else 1-t/T
        timefeature = torch.zeros((L)).float()
        timefeature[self.mask_str.squeeze()] = 1
        timefeature[~self.mask_str.squeeze()] = 1 - t/self.T
        timefeature = timefeature[None,None,...,None]

        t1d = torch.cat((t1d, timefeature), dim=-1).float()
        
        #############
        ### xyz_t ###
        #############
        if self.preprocess_conf.sidechain_input:
            xyz_t[torch.where(seq[:,21] == 1, True, False),3:,:] = float('nan')
        else:
            xyz_t[~self.mask_str.squeeze(),3:,:] = float('nan')

        xyz_t=xyz_t[None, None]
        xyz_t = torch.cat((xyz_t, torch.full((1,1,L,13,3), float('nan'))), dim=3)

        ###########
        ### t2d ###
        ###########
        t2d = xyz_to_t2d(xyz_t)
        
        ###########      
        ### idx ###
        ###########
        idx = torch.tensor(self.contig_map.rf)[None]

        ###############
        ### alpha_t ###
        ###############
        seq_tmp = t1d[...,:-1].argmax(dim=-1).reshape(-1,L)
        alpha, _, alpha_mask, _ = util.get_torsions(xyz_t.reshape(-1, L, 27, 3), seq_tmp, TOR_INDICES, TOR_CAN_FLIP, REF_ANGLES)
        alpha_mask = torch.logical_and(alpha_mask, ~torch.isnan(alpha[...,0]))
        alpha[torch.isnan(alpha)] = 0.0
        alpha = alpha.reshape(1,-1,L,10,2)
        alpha_mask = alpha_mask.reshape(1,-1,L,10,1)
        alpha_t = torch.cat((alpha, alpha_mask), dim=-1).reshape(1, -1, L, 30)

        #put tensors on device
        msa_masked = msa_masked.to(self.device)
        msa_full = msa_full.to(self.device)
        seq = seq.to(self.device)
        xyz_t = xyz_t.to(self.device)
        idx = idx.to(self.device)
        t1d = t1d.to(self.device)
        t2d = t2d.to(self.device)
        alpha_t = alpha_t.to(self.device)
        
        ######################
        ### added_features ###
        ######################
        if self.preprocess_conf.d_t1d >= 24: # add hotspot residues
            hotspot_tens = torch.zeros(L).float()
            if self.ppi_conf.hotspot_res is None:
                print("WARNING: you're using a model trained on complexes and hotspot residues, without specifying hotspots.\
                         If you're doing monomer diffusion this is fine")
                hotspot_idx=[]
            else:
                hotspots = [(i[0],int(i[1:])) for i in self.ppi_conf.hotspot_res]
                hotspot_idx=[]
                for i,res in enumerate(self.contig_map.con_ref_pdb_idx):
                    if res in hotspots:
                        hotspot_idx.append(self.contig_map.hal_idx0[i])
                hotspot_tens[hotspot_idx] = 1.0

            # Add blank (legacy) feature and hotspot tensor
            t1d=torch.cat((t1d, torch.zeros_like(t1d[...,:1]), hotspot_tens[None,None,...,None].to(self.device)), dim=-1)
        return msa_masked, msa_full, seq[None], torch.squeeze(xyz_t, dim=0), idx, t1d, t2d, xyz_t, alpha_t
    
    
    def _preprocess_batch(self, seq, xyz_t, t, mask=None,repack=False):
        
        """
        Function to prepare inputs to diffusion model
        
            seq (B,L,22) one-hot sequence 

            msa_masked (B,1,L,48)

            msa_full (B,1,L,25)
        
            xyz_t (B,L,14,3) template crds (diffused) 

            t1d (1,L,28) this is the t1d before tacking on the chi angles:
                - seq + unknown/mask (21)
                - global timestep (1-t/T if not motif else 1) (1)

                MODEL SPECIFIC:
                - contacting residues: for ppi. Target residues in contact with binder (1)
                - empty feature (legacy) (1)
                - ss (H, E, L, MASK) (4)
            
            t2d (1, L, L, 45)
                - last plane is block adjacency
    """

        B,L = seq.shape[:2]
        T = self.T
        binderlen = self.binderlen
        target_res = self.ppi_conf.hotspot_res
        device = seq.device
        ##################
        ### msa_masked ###
        ##################
        msa_masked = torch.zeros((B,1,L,48),device=device)
        msa_masked[:,:,:,:22] = seq.unsqueeze(1)
        msa_masked[:,:,:,22:44] = seq.unsqueeze(1)
        msa_masked[:,:,0,46] = 1.0
        msa_masked[:,:,-1,47] = 1.0

        ################
        ### msa_full ###
        ################
        msa_full = torch.zeros((B,1,L,25),device=self.device)
        msa_full[:,:,:,:22] = seq.unsqueeze(1)
        msa_full[:,:,0,23] = 1.0
        msa_full[:,:,-1,24] = 1.0

        ###########
        ### t1d ###
        ########### 

        # Here we need to go from one hot with 22 classes to one hot with 21 classes (last plane is missing token)
        t1d = torch.zeros((B,1,L,21),device=self.device)

        seqt1d = torch.clone(seq.unsqueeze(1))
        # print("seq1d",seqt1d.shape)
        # for idx in range(L):
        #     print(seqt1d[:,:,idx,21])
        #     if seqt1d[:,:,idx,21] == 1:
        #         seqt1d[:,:,idx,20] = 1
        #         seqt1d[:,:,idx,21] = 0
        t1d_condition = seqt1d[..., 21] == 1 
        
        seqt1d[..., 21][t1d_condition] = 0  
        seqt1d[..., 20][t1d_condition] = 1   
        
        t1d[:,:,:,:21] = seqt1d[:,:,:,:21]

        # Set timestep feature to 1 where diffusion mask is True, else 1-t/T
        self.mask_str = mask
        timefeature = torch.zeros((L),device=self.device).float()
        timefeature[self.mask_str.squeeze()] = 1
        timefeature[~self.mask_str.squeeze()] = 1 - t/self.T
        timefeature = timefeature[None,None,...,None].repeat(B,1,1,1)
        t1d = torch.cat((t1d, timefeature), dim=-1).float()
        
        #############
        ### xyz_t ###
        #############
        # if self.preprocess_conf.sidechain_input:
        #     mask = (seq[:, :, 21] == 1).unsqueeze(-1).unsqueeze(-1)  # shape [4, 256, 1, 1]
        #     xyz_t[:, :, 3:, :] = xyz_t[:, :, 3:, :].masked_fill(mask, float('nan'))
        # else:
        #     xyz_t[:,~self.mask_str.squeeze(),3:,:] = float('nan')

        xyz_t = torch.cat((xyz_t, torch.full((B,L,13,3), float('nan'),device=self.device )), dim=2)
        ###########
        ### t2d ###
        ###########
        t2d = xyz_to_t2d(xyz_t.unsqueeze(1))
        
        ###########      
        ### idx ###
        ###########
        # idx = torch.tensor(self.contig_map.rf)[None].repeat(B,1)
        idx = torch.arange(L)[None].repeat(B,1)


        ###############
        ### alpha_t ###
        ###############
        seq_tmp = t1d[...,:-1].argmax(dim=-1).reshape(-1,L)
        alpha, _, alpha_mask, _ = util.get_torsions(xyz_t.reshape(-1, L, 27, 3).to('cpu'), seq_tmp.to('cpu'), TOR_INDICES, TOR_CAN_FLIP, REF_ANGLES)
        alpha_mask = torch.logical_and(alpha_mask, ~torch.isnan(alpha[...,0]))
        alpha[torch.isnan(alpha)] = 0.0
        alpha = alpha.reshape(1,-1,L,10,2)
        alpha_mask = alpha_mask.reshape(1,-1,L,10,1)
        alpha_t = torch.cat((alpha, alpha_mask), dim=-1).reshape(B, -1, L, 30)

        #put tensors on device
        msa_masked = msa_masked.to(self.device)
        msa_full = msa_full.to(self.device)
        seq = seq.to(self.device)
        xyz_t = xyz_t.to(self.device)
        idx = idx.to(self.device)
        t1d = t1d.to(self.device)
        t2d = t2d.to(self.device)
        alpha_t = alpha_t.to(self.device)
        
        # ######################
        # ### added_features ###
        # ######################
        # if self.preprocess_conf.d_t1d >= 24: # add hotspot residues
        #     hotspot_tens = torch.zeros(L).float()
        #     if self.ppi_conf.hotspot_res is None:
        #         print("WARNING: you're using a model trained on complexes and hotspot residues, without specifying hotspots.\
        #                  If you're doing monomer diffusion this is fine")
        #         hotspot_idx=[]
        #     else:
        #         hotspots = [(i[0],int(i[1:])) for i in self.ppi_conf.hotspot_res]
        #         hotspot_idx=[]
        #         for i,res in enumerate(self.contig_map.con_ref_pdb_idx):
        #             if res in hotspots:
        #                 hotspot_idx.append(self.contig_map.hal_idx0[i])
        #         hotspot_tens[hotspot_idx] = 1.0

        #     # Add blank (legacy) feature and hotspot tensor
        #     t1d=torch.cat((t1d, torch.zeros_like(t1d[...,:1]), hotspot_tens[None,None,...,None].to(self.device)), dim=-1)
        return msa_masked, msa_full, seq, torch.squeeze(xyz_t, dim=0), idx, t1d, t2d, xyz_t.unsqueeze(1), alpha_t

    # def sample_step(self, *, t, x_t, seq_init, final_step, train=True):
    def sample_step(self, *, t, x_t, seq_t, bond_mat_t ,final_step, train=True):
        '''Generate the next pose that the model should be supplied at timestep t-1.

        Args:
            t (int): The timestep that has just been predicted
            seq_t (torch.tensor): (L,22) The sequence at the beginning of this timestep
            x_t (torch.tensor): (L,14,3) The residue positions at the beginning of this timestep
            seq_init (torch.tensor): (L,22) The initialized sequence used in updating the sequence.
            
        Returns:
            px0: (L,14,3) The model's prediction of x0.
            x_t_1: (L,14,3) The updated positions of the next step.
            seq_t_1: (L,22) The updated sequence of the next step.
            tors_t_1: (L, ?) The updated torsion angles of the next  step.
            plddt: (L, 1) Predicted lDDT of x0.
        '''
        # msa_masked, msa_full, seq_in, xt_in, idx_pdb, t1d, t2d, xyz_t, alpha_t = self._preprocess(
        #     seq_init, x_t, t)
        msa_masked, msa_full, seq_in, xt_in, idx_pdb, t1d, t2d, xyz_t, alpha_t = self._preprocess(
            seq_t, x_t, t)
        
        bond_mat_t = bond_mat_t.to(xyz_t.device)

        N,L = msa_masked.shape[:2]

        if self.symmetry is not None:
            idx_pdb, self.chain_idx = self.symmetry.res_idx_procesing(res_idx=idx_pdb)

        msa_prev = None
        pair_prev = None
        state_prev = None
        print("msa_masked",msa_masked.shape)
        print("msa_full",msa_full.shape)
        # with torch.no_grad():
        msa_prev, pair_prev, px0, state_prev, alpha, logits, bond_mat, plddt = self.model(
                            msa_latent=msa_masked,
                            msa_full=msa_full,
                            seq=seq_in,
                            xyz=xt_in,
                            bond_mat=bond_mat_t,
                            idx=idx_pdb,
                            t=torch.tensor(t),
                            t1d=t1d,
                            t2d=t2d,
                            xyz_t=xyz_t,
                            alpha_t=alpha_t,
                            msa_prev = msa_prev,
                            pair_prev = pair_prev,
                            state_prev = state_prev,
                            return_infer=True,
                            motif_mask=self.diffusion_mask.squeeze().to(self.device))

        # prediction of X0 
        pseq0 = torch.argmax(logits, dim=-1)
        # _, px0  = self.allatom(torch.argmax(seq_in, dim=-1), px0, alpha)
        _, px0  = self.allatom(pseq0 , px0, alpha)
        px0 = px0.squeeze()[:,:14]

        if train:
            return px0, pseq0, bond_mat, plddt
        else:
            #####################
            ### Get next pose ###
            # #####################
            seq_t_1 = torch.clone(seq_t)
            if t > final_step:
                #seq_t_1 = nn.one_hot(seq_init,num_classes=22).to(self.device)
                x_t_1, px0 = self.denoiser.get_next_pose(
                    xt=x_t,
                    px0=px0,
                    xt_grad = xt_in,
                    t=t,
                    diffusion_mask=self.mask_str.squeeze(),
                    align_motif=self.inf_conf.align_motif
                )
            else:
                x_t_1 = torch.clone(px0).to(x_t.device)
                seq_t_1 = torch.clone(seq_t)
                px0 = px0.to(x_t.device)

            if self.symmetry is not None:
                x_t_1, seq_t_1 = self.symmetry.apply_symmetry(x_t_1, seq_t_1)

            return px0, x_t_1, seq_t_1, bond_mat ,plddt


In [3]:
import hydra
from hydra import initialize, compose
from omegaconf import OmegaConf

def make_deterministic(seed=0):
    torch.manual_seed(seed)
    np.random.seed(seed)
    random.seed(seed)

def main(conf) -> None:  # 移除类型标注中的 HydraConfig
    log = logging.getLogger(__name__)
    if conf.inference.deterministic:
        make_deterministic()

    # Check for available GPU and print result of check
    if torch.cuda.is_available():
        device_name = torch.cuda.get_device_name(torch.cuda.current_device())
        log.info(f"Found GPU with device_name {device_name}. Will run RFdiffusion on {device_name}")
    else:
        log.info("////////////////////////////////////////////////")
        log.info("///// NO GPU DETECTED! Falling back to CPU /////")
        log.info("////////////////////////////////////////////////")

    # Initialize sampler and target/contig.
    sampler = MySampler(conf)
    sampler.sample_init()
    return sampler


In [4]:
with initialize(version_base=None, config_path="./config/inference"):
    cfg = compose(config_name="base")
print(cfg['diffuser'])
# 调用主函数
sampler = main(cfg)

{'T': 200, 'b_0': 0.01, 'b_T': 0.07, 'schedule_type': 'linear', 'so3_type': 'igso3', 'crd_scale': 0.25, 'partial_T': None, 'so3_schedule_type': 'linear', 'min_b': 1.5, 'max_b': 2.5, 'min_sigma': 0.02, 'max_sigma': 1.5}
Reading models from /WORK/PUBLIC/lulei_work/xjt/Protein_design/RFdiffusion/mytest/../models
This is inf_conf.ckpt_path
/WORK/PUBLIC/lulei_work/xjt/Protein_design/RFdiffusion/mytest/../models/Base_ckpt.pt
Successful diffuser __init__
With this beta schedule (linear schedule, beta_0 = 0.01, beta_T = 0.07), alpha_bar_T = 0.00027539944858290255


In [18]:
import torch
B,L,K=2,100,20
seq_pred = torch.ones((B, L,K))
seq_orig = torch.randint(0, K, (B, L))  # Random sequence for testing
mask = torch.ones((B, L), dtype=torch.bool)  # Example mask, all True
mask[0,3:] = False  # Set some positions to False for testing
seq_orig[0,3:]=100
from Loss import *

seqloss = LseqLoss()

loss = seqloss(seq_pred,seq_orig, mask)
print(f"Loss: {loss.item()}")

Loss: 2.9957315921783447


In [6]:
print(fa_stack[:,-1,:,1,:])

print(aaaa)

tensor([[[    -5.1181,     -1.6029,      2.2483],
         [     1.2130,     -1.8310,     -0.3827],
         [     1.7288,     -2.8123,     -0.9355],
         [   999.0000,    999.0000,    999.0000],
         [   999.0000,    999.0000,    999.0000]],

        [[     5.8519,      3.0032,      1.7850],
         [     4.5558,      3.6702,     -5.7163],
         [    -1.8028,      6.7948,      0.5695],
         [    -2.5467,      3.1936,      0.9514],
         [    -3.0086,      0.4766,     -1.5626]]])


NameError: name 'aaaa' is not defined

In [ ]:
from dataloader import *
import torch.multiprocessing as mp
from torch.utils.data.distributed import DistributedSampler
from torch.nn.parallel import DistributedDataParallel as DDP
from torch.distributed import init_process_group, destroy_process_group
data_dir = "/home/fit/lulei/WORK/xjt/Protein_design/CyclicPeptide/Dataset/ALL_PDB"
cluster_file = os.path.join(data_dir,"tmp/cluster.tsv")
pdb_feature_dir = os.path.join(data_dir,"PDB_FEATURE")
pdb_dir =  os.path.join(data_dir,"final_cleaned_PDB")
link_file_path = os.path.join(data_dir,"LINK/results.txt")
cache_dir = os.path.join(data_dir,"dataset_cache")
crop_size = 180
val_ratio = 0.1
split = 'train'

# 第一部分：获取数据集
dataset = get_or_create_dataset(
    cluster_file=cluster_file,
    pdb_feature_dir=pdb_feature_dir,
    pdb_dir=pdb_dir,
    link_file_path=link_file_path,
    crop_size=crop_size,
    cache_dir=cache_dir,
    val_ratio=val_ratio,
    split=split 
)
split = 'val'
dataset = get_or_create_dataset(
    cluster_file=cluster_file,
    pdb_feature_dir=pdb_feature_dir,
    pdb_dir=pdb_dir,
    link_file_path=link_file_path,
    crop_size=crop_size,
    cache_dir=cache_dir,
    val_ratio=val_ratio,
    split=split 
)




Creating new train dataset...
start construct Linkereader
1TON_A not equal
2P6Z_B not equal验证 1PY3_B 时出错: string index out of range



Traceback (most recent call last):
  File "/WORK/PUBLIC/lulei_work/xjt/Protein_design/RFdiffusion/mytest/dataloader.py", line 151, in _verify_single_chain
    res2_name_pdb = AA_1_TO_3[pdb_residue_map[res2_num_link]]
IndexError: string index out of range


2BXU_H not equal


KeyboardInterrupt: 

In [ ]:
# 第二部分：创建数据加载器
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
dataloader = create_dataloader_from_dataset(
    dataset=dataset,
    device=device ,
    batch_size=2,
    num_workers=0,
    num_samples=25600,
    DDP=False,
)

In [ ]:

from torch.optim.lr_scheduler import LambdaLR
from Loss import *
from torch.optim import Adam

# 初始化模型
model = sampler.model.to(device) 

# 学习率调度器配置
warmup_steps = 500      # 预热步数
decay_interval = 5000   # 衰减间隔
decay_rate = 0.95       # 衰减率

# 自定义学习率调度函数
def lr_lambda(step):
    # 线性预热阶段
    if step < warmup_steps:
        return float(step) / float(max(1, warmup_steps))
    # 周期性衰减阶段
    decay_factor = decay_rate ** (step // decay_interval)
    return decay_factor

optimizer = Adam(
    model.parameters(),
    lr=0.001,           # 初始学习率
    weight_decay=0.01    # L2正则化系数
)
scheduler = LambdaLR(optimizer, lr_lambda=lr_lambda)

criterion_frame = LFrameRTLoss(w_trans=0.5, w_rot=1.0)
criterion_2D = L2DLoss()


In [ ]:
import time

epochs = 140

use_amp = False
scaler = torch.amp.GradScaler("cuda" ,enabled=use_amp)

for epoch in range(epochs):
    for i, batch_data in enumerate(dataloader):

        optimizer.zero_grad()

        #partial_T 采样 U~(0,1)
        partial_T = int(torch.rand(1).item() * sampler.diffuser_conf.T)

        xyz_3 =torch.tensor(batch_data['pdb_xyz']).clone() # (B, L, 3, 3)
        seq_orig = torch.tensor(batch_data['sequence_ids']).clone()# (B, L)

        x_noise, seq_noise,seq_grad = sampler.sample_init_forward(xyz_3 , seq_orig, partial_T=partial_T,mask=batch_data['attention_mask'])

        msa_masked, msa_full, seq_in, xt_in, idx_pdb, t1d, t2d, xyz_t, alpha_t = sampler._preprocess_batch(
            seq_noise, x_noise, partial_T, mask=batch_data['attention_mask'])

        B, N, L, _ = msa_masked.shape
        #bond_mat_t = torch.zeros((B, L, L), dtype=torch.float32, device=sampler.device)  # (B, L, L)
        bond_mat_t = batch_data['bond_matrix'].to(sampler.device).float() # (B, L, L)

        msa_prev =  None
        pair_prev = None
        state_prev = None
        motif_mask = torch.zeros(L, dtype=torch.bool, device=sampler.device)
        # with torch.amp.autocast(device_type=str(sampler.device)):
        start = time.perf_counter()   # 高精度计时器（推荐）
        # with torch.no_grad():
        with torch.autocast(device_type=str(sampler.device), enabled=use_amp):
            # msa_prev, pair_prev, px0, state_prev, alpha, logits, bond_mat, plddt = sampler.model(
            logits_2d, logits_aa, logits_exp, T, R, alpha_s, bond_matrix, lddt = sampler.model(
                                msa_latent=msa_masked,
                                msa_full=msa_full,
                                seq=seq_in,
                                xyz=xt_in,
                                bond_mat=bond_mat_t,
                                idx=idx_pdb,
                                t=torch.tensor(partial_T).to(sampler.device),
                                t1d=t1d,
                                t2d=t2d,
                                xyz_t=xyz_t,
                                alpha_t=alpha_t,
                                msa_prev = msa_prev,
                                pair_prev = pair_prev,
                                state_prev = state_prev,
                                return_infer=False,
                                motif_mask=motif_mask,#sampler.diffusion_mask.squeeze().to(sampler.device),
                                batch_mask = batch_data['attention_mask'],
            )

        
        end = time.perf_counter() 
        print(f"耗时: {end - start:.6f} 秒")
        times = R.size(0)
        loss_frame = criterion_frame((R.permute(1,0,2,3,4), T.permute(1,0,2,3)), 
                                    (batch_data['rotations'].permute(0,1,2,3).unsqueeze(1).expand(-1,times,-1,-1,-1),
                                    batch_data['translations'].unsqueeze(1).expand(-1,times,-1,-1)),
                                    mask = batch_data['attention_mask'].bool()
        )

        mask_2d = (batch_data['attention_mask'].unsqueeze(2).float() @ batch_data['attention_mask'].unsqueeze(1).float() ).bool()
        logits_dist, logits_omega, logits_theta, logits_phi = logits_2d
        loss_2d =criterion_2D(logits_dist, logits_omega, logits_theta, logits_phi,
                                batch_data['dist_matrix_cb'],batch_data['l2d_omega_matrix'],batch_data['l2d_theta_matrix'],batch_data['l2d_phi_matrix'],
                                mask_2d = mask_2d)
                                


        end2 = time.perf_counter()
        print(f"耗时: {end2 - end:.6f} 秒")
        total_loss = loss_frame + loss_2d
        total_loss.backward()
        # scheduler.step()
        # optimizer.step()
        # end3 = time.perf_counter()
        # print(f"耗时: {end3 - end2:.6f} 秒")
        print("loss frame",loss_frame.item())


    #     break
    # break


<__array_function__ internals>:200: RuntimeWarning: invalid value encountered in cast
/tmp/ipykernel_3317171/4611874.py:16: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  xyz_3 =torch.tensor(batch_data['pdb_xyz']).clone() # (B, L, 3, 3)
/tmp/ipykernel_3317171/4611874.py:17: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  seq_orig = torch.tensor(batch_data['sequence_ids']).clone()# (B, L)


KeyboardInterrupt: 

In [ ]:
# logits_2d, logits_aa, logits_exp, T, R, alpha_s, bond_matrix, lddt
for i in range(len(logits_2d)):
    print(f"logits_2d{i}", logits_2d[i].shape)
print("logits_aa", logits_aa.shape)
print("logits_exp", logits_exp.shape)
print("T", T.shape)
print("R", R.shape)
print("alpha_s", alpha_s.shape)
print("bond_matrix", bond_matrix.shape)
print("lddt", lddt.shape)


logits_2d0 torch.Size([2, 37, 180, 180])
logits_2d1 torch.Size([2, 37, 180, 180])
logits_2d2 torch.Size([2, 37, 180, 180])
logits_2d3 torch.Size([2, 19, 180, 180])
logits_aa torch.Size([2, 21, 180])
logits_exp torch.Size([2, 180])
T torch.Size([40, 2, 180, 3])
R torch.Size([40, 2, 180, 3, 3])
alpha_s torch.Size([40, 2, 180, 10, 2])
bond_matrix torch.Size([2, 2, 180, 180])
lddt torch.Size([2, 50, 180])


In [ ]:
import os 
os.environ['CUDA_LAUNCH_BLOCKING']  = '1'
torch.set_printoptions(profile="full")
print(batch_data)
torch.set_printoptions(profile="default") # reset

{'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0],
        [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
         1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,

In [ ]:
def count_nan_statistics(tensor_dict):
    """统计张量中NaN值的详细信息"""
    print("=" * 80)
    print("NaN Statistics Summary")
    print("=" * 80)
    
    total_nan_count = 0
    total_element_count = 0
    
    for name, tensor in tensor_dict.items():
        if tensor is None:
            print(f"{name:<12}: None")
            continue
            
        # 基本信息
        shape = tensor.shape
        total_elements = tensor.numel()
        nan_count = torch.isnan(tensor).sum().item()
        nan_percentage = (nan_count / total_elements) * 100 if total_elements > 0 else 0
        
        # 累计统计
        total_nan_count += nan_count
        total_element_count += total_elements
        
        print(f"{name:<12}: Shape={str(shape):<20} "
              f"Total={total_elements:<8} "
              f"NaN={nan_count:<8} "
              f"NaN%={nan_percentage:.2f}%")
        
        # 如果有NaN，显示每个维度的NaN分布
        if nan_count > 0:
            nan_mask = torch.isnan(tensor)
            
            # 按最后几个维度统计NaN
            if len(shape) >= 2:
                # 展平除了最后一个维度的所有维度
                reshaped = tensor.view(-1, shape[-1])
                nan_reshaped = nan_mask.view(-1, shape[-1])
                
                # 统计每个特征维度的NaN数量
                nan_per_feature = nan_reshaped.sum(dim=0)
                if nan_per_feature.sum() > 0:
                    non_zero_features = (nan_per_feature > 0).nonzero().flatten()
                    if len(non_zero_features) > 0:
                        print(f"  └─ NaN per feature dim: {dict(zip(non_zero_features.tolist(), nan_per_feature[non_zero_features].tolist()))}")
    
    print("-" * 80)
    overall_percentage = (total_nan_count / total_element_count) * 100 if total_element_count > 0 else 0
    print(f"{'OVERALL':<12}: Total Elements={total_element_count:<8} "
          f"Total NaN={total_nan_count:<8} "
          f"Overall NaN%={overall_percentage:.2f}%")
    print("=" * 80)



# 创建张量字典进行统计
tensor_dict = {
    'msa_masked': msa_masked,
    'msa_full': msa_full, 
    'seq_in': seq_in,
    'xt_in': xt_in,
    'idx_pdb': idx_pdb,
    't1d': t1d,
    't2d': t2d,
    'xyz_t': xyz_t,
    'alpha_t': alpha_t
}
result_dict={
    'msa_prev':msa_prev,
    'pair_prev':pair_prev,
    'px0': px0,
    'state_prev': state_prev,
    'alpha': alpha,
    'logits': logits,
    'bond_mat': bond_mat,
    'plddt': plddt 

}

# 统计NaN信息
count_nan_statistics(result_dict)

# 如果你还想看具体的张量值，可以选择性打印
print("\nDetailed tensor values (only non-NaN parts):")
for name, tensor in tensor_dict.items():
    if tensor is not None and torch.isnan(tensor).sum() > 0:
        print(f"\n{name} (showing first few non-NaN values):")
        non_nan_mask = ~torch.isnan(tensor)
        if non_nan_mask.any():
            non_nan_values = tensor[non_nan_mask][:10]  # 只显示前10个非NaN值
            print(f"  Sample non-NaN values: {non_nan_values}")

# ...existing code...


NameError: name 'px0' is not defined

In [9]:
import torch
B,L,K=2,5,3
a = torch.ones((B, L,K))
b = torch.zeros((B, L,K))
mask = torch.ones((B, L), dtype=torch.bool)  # Example mask, all True
a[:,:,:] = b[mask,:]
print(a.shape)

RuntimeError: The expanded size of the tensor (5) must match the existing size (10) at non-singleton dimension 1.  Target sizes: [2, 5, 3].  Tensor sizes: [10, 3]

In [1]:
[1] + [1]

[1, 1]